<a href="https://colab.research.google.com/github/HausReport/ClubRaiders/blob/master/notebooks/History.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [36]:
import sys

!{sys.executable} -m pip install --force-reinstall --upgrade "git+https://github.com/HausReport/ClubRaiders.git#egg=craid"
import craid.eddb.loader.DataProducer as dp
import pandas as pd
import logging
import plotly.graph_objs as go
import plotly.express as px
import numpy as np
from dateutil.relativedelta import relativedelta
from datetime import timedelta, date
import datetime as dt

logging.getLogger().addHandler(logging.StreamHandler())
logging.getLogger().level = logging.DEBUG

arrays = dp.getDataArrays()
baseFrame: pd.DataFrame = arrays['dataFrame']

  Cloning https://github.com/HausReport/ClubRaiders.git to /tmp/pip-install-w_1pvtd5/craid
  Running command git clone -q https://github.com/HausReport/ClubRaiders.git /tmp/pip-install-w_1pvtd5/craid
Processing /root/.cache/pip/wheels/8f/56/d1/def235a9ef977abf4476d1ad7a3ad8d9af7537445ce01c5e16/dash-1.16.3-cp36-none-any.whl
Processing /root/.cache/pip/wheels/29/11/a0/0cf8183b6f7df4716bec25b0e089043cd161bb58accc6633a6/dash_core_components-1.12.1-cp36-none-any.whl
Processing /root/.cache/pip/wheels/8d/01/46/78e4de185a8a4a2da8ba31da16c52170f036d4cebeeb6e07a2/dash_html_components-1.1.1-cp36-none-any.whl
Processing /root/.cache/pip/wheels/3d/c2/fd/50a7ea0b9aef63cf3bf3c5fb22799b8ba9a97ea8f9b14b7124/dash_table-4.10.1-cp36-none-any.whl
Processing /root/.cache/pip/wheels/c8/8f/0f/9cf71e7362b302350e10fcc9ca7f0377b84a6ea14445c2d6aa/dash_renderer-1.8.2-cp36-none-any.whl
  Using cached https://files.pythonhosted.org/packages/f2/28/2a03252dfb9ebf377f40fba6a7841b47083260bf8bd8e737b0c6952df83f/Flask-1.

Acquired lock.
Acquired lock.
Loading from AWS
Loading from AWS
Memory tracker: 0:239,910,912
Memory tracker: 0:239,910,912
Found data file: /tmp/smol-factions.jsonl.gz
Found data file: /tmp/smol-factions.jsonl.gz
Read 627 lines of faction data
Read 627 lines of faction data
Memory tracker: 0.5:239,910,912
Memory tracker: 0.5:239,910,912
Found data file: /tmp/smol-systems_populated.jsonl.gz
Found data file: /tmp/smol-systems_populated.jsonl.gz
Read 166 lines of systems data
Read 166 lines of systems data
Memory tracker: 1:240,807,936
Memory tracker: 1:240,807,936
Populated club system keys
Populated club system keys
Club system lookup set has {166} items
Club system lookup set has {166} items
Populated faction instances: {992} items.
Populated faction instances: {992} items.
Memory tracker: 2:240,807,936
Memory tracker: 2:240,807,936
Found data file: /tmp/smol-stations.jsonl.gz
Found data file: /tmp/smol-stations.jsonl.gz
Read 552 lines of station data, adding 552
Read 552 lines of sta

In [37]:
#pip install "pandas-profiling"


In [38]:
from craid.eddb.loader.strategy.DataLoader import DataLoader
from craid.eddb.loader.strategy.GithubLoader import LoadDataFromGithub
from craid.history.History import History

myLoader = LoadDataFromGithub(_forceWebDownload=True, useSmol=False)
hist = History()
csa = hist.getRawDataFrame()
target = hist.getNormalizedDataFrame()

In [39]:
def getHistoryForFacationAndSystem(fac: str, sys: str):
  hist = History()
  tmp = hist.getRawDataFrame()
  return tmp[ (tmp['faction']==fac) & (tmp['system']==sys)]

def getHistoryForFacation(fac: str):
  hist = History()
  tmp = hist.getRawDataFrame()
  return tmp[ (tmp['faction']==fac)]

def getHistoryForSystem(sys: str):
  hist = History()
  tmp = hist.getRawDataFrame()
  return tmp[tmp['system']==sys]

def getHistoryForRegion(reg: int):
  hist = History()
  tmp = hist.getRawDataFrame()
  return tmp[tmp['region']==reg]

def getLatestInfluences():
  hist = History()
  csa = hist.getRawDataFrame()
  stage1 = csa.loc[csa.groupby(['faction','system']).updated.idxmax()]
  return stage1.sort_values(['faction','system'])

def getLatestInfluenceBefore(dateStr:str):
  hist = History()
  csa = hist.getRawDataFrame()
  csa = csa [ csa['updated']<= dateStr]
  #csa = csa[ csa['updated'<dateStr]]
  stage1 = csa.loc[csa.groupby(['faction','system']).updated.idxmax()]
  return stage1.sort_values(['faction','system'])

def getClubInfluenceOnDate(dateStr: str):
  #reg = csa[ csa['region']== 1]
  hist = History()
  csa = getLatestInfluenceBefore(dateStr)
  stage1 = csa.loc[csa.groupby(['faction','system']).updated.idxmax()]
  stage3 = stage1[['system','faction','influence']].groupby('faction').influence.sum().reset_index()
  return stage3.influence.sum()

def getHistoryByWeek():
  hist = History()
  tmp = hist.getRawDataFrame().copy()
  tmp['week'] = pd.to_datetime(tmp.updated).dt.to_period('W').dt.to_timestamp()
  tmp = tmp.loc[tmp.groupby(['faction', 'system','week']).updated.idxmax()]
  tmp.updated = tmp.week
  return tmp.sort_values(['faction','system'])

def getHistoryByMonth():
  hist = History()
  tmp = hist.getRawDataFrame().copy()
  tmp['month'] = pd.to_datetime(tmp.updated).dt.to_period('M').dt.to_timestamp()
  tmp = tmp.loc[tmp.groupby(['faction', 'system','month']).updated.idxmax()]
  return tmp.sort_values(['faction','system'])


In [40]:
def getScroller(fig):
  fig.update_layout(
    xaxis=dict(
        rangeselector=dict(
            buttons=list([
                dict(count=1,
                     label="1m",
                     step="month",
                     stepmode="backward"),
                dict(count=6,
                     label="6m",
                     step="month",
                     stepmode="backward"),
                dict(count=1,
                     label="YTD",
                     step="year",
                     stepmode="todate"),
                dict(count=1,
                     label="1y",
                     step="year",
                     stepmode="backward"),
                dict(step="all")
            ])
        ),
        rangeslider=dict(
            visible=True
        ),
        type="date"
  ))

In [41]:
def getFactionInfluenceGraph(fac: str):
  ogun = getHistoryForFacation(fac)
  #ogun = target[ target['faction']==fac]
  a = ogun['system'].unique().tolist()
  fig = go.Figure()
  for sys in a:
    theSlice = ogun[ ogun['system'] == sys].reset_index()
    fig.add_trace(go.Scatter(x=theSlice['updated'], y=theSlice['influence'],
                    mode='lines',
                    stackgroup="b",
                    name=sys,
                    stackgaps='interpolate'))
  getScroller(fig)
  return fig

In [42]:
def getSystemInfluenceGraph(sys: str):
  #ogun = target[ target['system']==sys]
  ogun = getHistoryForSystem(sys)
  a = ogun['faction'].unique().tolist()
  fig = go.Figure()
  for fac in a:
    theSlice = ogun[ ogun['faction'] == fac].reset_index()
    fig.add_trace(go.Scatter(x=theSlice['updated'], y=theSlice['influence'],
                    mode='lines',
                    name=fac))
  getScroller(fig)
  return fig

In [43]:
def getClubInfluencePieChart():
  stage1 = getLatestInfluences() 
  stage3 = stage1[['system','faction','influence']].groupby('faction').influence.sum().reset_index()
  fig = px.pie(stage3, values='influence', names='faction', title='Total Influence by Minor Faction', width=350, height=350)
  fig.update_traces(textposition="inside")
  fig.update_layout(showlegend=False)
  return fig


In [44]:
fig = getClubInfluencePieChart()
fig.show()

In [45]:
from craid.club.regions.RegionFactory import RegionFactory
stage1 = getLatestInfluences() 
stage3 = stage1[['region','influence']].groupby('region').influence.sum().reset_index()
dicts = [ {'region': 7, 'influence': 0.0}]
stage3 = stage3.append(dicts, ignore_index=True, sort=False)
stage3 = stage3.sort_values(['region'])
regionNames = list(RegionFactory.regionDict.keys())
fig = px.pie(stage3, values='influence', names=regionNames, title='Total Club Influence by Region', width=350, height=350) #, names='faction'
fig.update_traces(textposition="inside")
fig.update_layout(showlegend=False)
fig.show()

In [46]:
region = 1
regionNames = list(RegionFactory.regionDict.keys())
regionName = regionNames[region]
title = f"Total Influence <br>by Minor Faction <br>in the {regionName} region"
merope = getHistoryForRegion(region) # target[ target['region']== region]
#stage1 = merope.loc[merope.groupby(['faction','system']).updated.idxmax()]
stage3 = merope[['system','faction','influence']].groupby('faction').influence.sum().reset_index()
fig = px.pie(stage3, values='influence', names='faction', title=title, width=350, height=350) #, names='faction'
fig.update_traces(textposition="inside")
fig.update_layout(showlegend=False)
fig.show()

In [47]:
theDate = '2020-06-1'
getClubInfluenceOnDate(theDate)

4236.007999040682

In [48]:
theDate = '2020-10-22'
getClubInfluenceOnDate(theDate)

4800.770499040681

In [49]:
region = 8

dates = []
inf = []

start_date = date(2018, 5, 15)
daily_date = date(2020,5,30)
end_date = date.today() + timedelta(days=1) 

dframe = getHistoryForRegion(region)#   csa[ csa['region'] == region]
regionNames = list(RegionFactory.regionDict.keys())
regionName = regionNames[region]
title = f"Total Club Influence in the {regionName} region"

single_date = start_date
while single_date <= end_date:
    theDate = single_date.strftime("%Y-%m-%d")
    dated = dframe [ dframe['updated']<= theDate]

    stage1 = dated.loc[dated.groupby(['faction','system']).updated.idxmax()]
    stage3 = stage1[['system','faction','influence']].groupby('faction').influence.sum().reset_index()
    theInf = stage3.influence.sum()
    dates.append(theDate)
    inf.append(theInf)
    if(single_date<daily_date):
      single_date = single_date + relativedelta(months=1)
    else:
      single_date = single_date + relativedelta(days=1)
      
labels = {'x':'Day', 'y':"Total Influence"}
fig = px.line(x=dates, y=inf, title=title, labels=labels)
fig.show()

In [50]:

dates = []
inf = []

start_date = date(2018, 5, 15)
daily_date = date(2020,5,30)
end_date = date.today() + timedelta(days=1) 

dframe = getHistoryForRegion(region)
regionNames = list(RegionFactory.regionDict.keys())
regionName = regionNames[region]
title = f"Total Club Influence"

single_date = start_date
while single_date <= end_date:
    theDate = single_date.strftime("%Y-%m-%d")
    dated = dframe [ dframe['updated']<= theDate]

    stage1 = dated.loc[dated.groupby(['faction','system']).updated.idxmax()]
    stage3 = stage1[['system','faction','influence']].groupby('faction').influence.sum().reset_index()
    theInf = stage3.influence.sum()
    dates.append(theDate)
    inf.append(theInf)
    if(single_date<daily_date):
      single_date = single_date + relativedelta(months=1)
    else:
      single_date = single_date + relativedelta(days=1)

labels = {'x':'Day', 'y':"Total Influence"}
fig = px.line(x=dates, y=inf, title=title, labels=labels)
fig.show()

In [51]:
dates = []
inf = []

faction = "Sirius Corporation"
faction = "Hodack Prison Colony"
faction = "Wreaken Construction"
#faction = "'Sirius Drives'"
faction = "Aegis Core"
#faction = "Aegis Research"
#faction = "Bill Turner"

start_date = date(2018, 5, 15)
daily_date = date(2020,5,30)
end_date = date.today() + timedelta(days=1) #date(2020, 6, 28)

dframe = getHistoryForFacation(faction)
#dframe = getHistoryForFaction(faction)
regionNames = list(RegionFactory.regionDict.keys())
regionName = regionNames[region]
title = f"Total Influence of the {faction} Faction"

single_date = start_date
while single_date <= end_date:
    theDate = single_date.strftime("%Y-%m-%d")
    dated = dframe [ dframe['updated']<= theDate]

    stage1 = dated.loc[dated.groupby(['faction','system']).updated.idxmax()]
    stage3 = stage1[['system','faction','influence']].groupby('faction').influence.sum().reset_index()
    theInf = stage3.influence.sum()
    dates.append(theDate)
    inf.append(theInf)
    if(single_date<daily_date):
      single_date = single_date + relativedelta(months=1)
    else:
      single_date = single_date + relativedelta(days=1)


labels = {'x':'Day', 'y':"Total Influence"}
fig = px.line(x=dates, y=inf, title=title, labels=labels)
fig.show()

In [52]:
getFactionInfluenceGraph("Aegis Core").show()

In [53]:
badGuys= ['Abroin Universal PLC',
                     'Aegis Core', 'Aegis Defense', 'Aegis Research',
                      'Bill Turner',
                     'CQC Holdings',
                     'Gallant Investment Brokers', 'Hodack Prison Colony',
                     'Janus Incorporated', "Namarii Emperor's Dawn",
                     'Pleiades Resource Enterprise',
                     'Reyan BPS', 'Reynhardt IntelliSys',
                     'Sirius Atmospherics', 'Sirius Catering', 'Sirius Corporation',
                     'Sirius Drives', 'Sirius Hot2Cold', 'Sirius Hyperspace',
                     'Sirius Industrial', 'Sirius Luxury Transports', 'Sirius Mining Merope',
                     'Sirius Mining', 'Sirius Power',
                     'The Greenventure Group',
                     'The Peterson Group', 'The Rockforth Corporation',
                     'Turner Research Group', 'Wiggins Development Trust',
                     'Wreaken Construction'
                     ]

In [54]:
a = csa['faction'].unique().tolist()
b = baseFrame['factionName'].unique().tolist()
aa = set(a)
bb = set(b)
bb-aa

set()

In [55]:
dates = []
inf = []

faction = "Combined Sirius Factions"
faction1 = "Sirius"

start_date = date(2018, 5, 15)
daily_date = date(2020,5,30)
end_date = date.today() + timedelta(days=1) #date(2020, 6, 28)


dframe = target[ (target['faction'].str.contains(faction1)) ]
regionNames = list(RegionFactory.regionDict.keys())
regionName = regionNames[region]
title = f"Total Influence of the {faction} Faction"

single_date = start_date
while single_date <= end_date:
    theDate = single_date.strftime("%Y-%m-%d")
    dated = dframe [ dframe['updated']<= theDate]

    stage1 = dated.loc[dated.groupby(['faction','system']).updated.idxmax()]
    stage3 = stage1[['system','faction','influence']].groupby('faction').influence.sum().reset_index()
    theInf = stage3.influence.sum()
    dates.append(theDate)
    inf.append(theInf)
    if(single_date<daily_date):
      single_date = single_date + relativedelta(months=1)
    else:
      single_date = single_date + relativedelta(days=1)


labels = {'x':'Day', 'y':"Total Influence"}
fig = px.line(x=dates, y=inf, title=title, labels=labels)
fig.show()

In [56]:
# One System, handles Multiple Factions
fig = getSystemInfluenceGraph("Celaeno")
fig.show()

In [57]:
fig = getSystemInfluenceGraph("Solati")
fig.show()

In [58]:
# One System, handles Multiple Factions
fig = getSystemInfluenceGraph("Sol")
fig.show()

In [59]:
getFactionInfluenceGraph('Hodack Prison Colony').show()

In [60]:
fac = 'Sirius Mining'

fac = 'CQC Holdings'
fac = 'Aegis Core'
fac = 'Sirius Mining Merope'

getFactionInfluenceGraph(fac).show()

In [61]:
from typing import List
def getCombinedFactionGraph( factions: List[str], titleSubject=None):
  labels = {'x':'Day', 'y':"Total Influence"}
  fig = go.Figure()
  for fac in factions:
    foo = getHistoryForFacation(fac)    #target[target['faction']== fac]
    stage3 = foo[['system','faction','influence','updated']].groupby(['updated']).influence.sum().reset_index()
    fig.add_trace(go.Scatter(x=stage3['updated'], y=stage3['influence'],
                    mode='lines',
                    stackgroup="b",
                    name=fac,
                    stackgaps="interpolate"))

  if titleSubject is None:
    titleSubject = "+".join(factions)

  title = f"Total influence of {titleSubject}"
  fig.update_layout(title=title,
                    xaxis_title="Date",
                    yaxis_title="Total Influence")
  getScroller(fig)
  return fig



In [62]:
factions = ["Wreaken Construction", "Hodack Prison Colony"]

fig = getCombinedFactionGraph( factions, titleSubject=None)
fig.show()

In [63]:
siriusFactions = ['Sirius Atmospherics', 'Sirius Catering',
       'Sirius Corporation', 'Sirius Drives', 'Sirius Hot2Cold',
       'Sirius Hyperspace', 'Sirius Industrial',
       'Sirius Luxury Transports', 'Sirius Mining Merope',
       'Sirius Mining', 'Sirius Power']
      
fig = getCombinedFactionGraph( siriusFactions, titleSubject="Combined Sirius Factions")
fig.show()

In [64]:
pd.set_option('mode.chained_assignment', None)

#from craid.eddb.loader.strategy.AWSLoader import LoadDataFromAWS
#loader = LoadDataFromAWS(forceWebDownload=False, useSmol=False)
#fName = loader.find_data_file('history.jsonl')
#dataframe = pd.read_json(fName, lines=True, compression='infer')
#dataframe = dataframe[ dataframe.faction != "Benton's Gang"]
#dataframe = dataframe[ dataframe.faction != "Bentonian Party"]
#dataframe = dataframe[ dataframe.faction != "Worster Insurance"]

pd.set_option('max_rows', 99999)
pd.set_option('max_colwidth', 400)

#dataframe = dataframe.rename(columns={'string':'system',
#                          'string':'faction',
#                          'datetime': 'updated', 
#                          'float':'influence',
#                          'boolean':'control',
#                          'int':'region',
#                          'float': 'population'})

In [65]:
getFactionInfluenceGraph("Sirius Mining Merope").show()

In [66]:
getFactionInfluenceGraph("Sirius Hyperspace").show()

In [67]:
getFactionInfluenceGraph("Pleiades Resource Enterprise").show()

In [68]:
#mf = tf
##mf['updated'] = tf.updated.dt.round('MS')
#mf['updated'] = pd.to_datetime(mf.updated).dt.to_period('M').dt.to_timestamp()
#mf = mf.drop_duplicates(subset=['system', 'faction', 'updated'])
#hurm = mf.groupby(['updated','faction']).count().reset_index()
#hurm

In [69]:
def factionPresenceGraph( faction: str):

  #
  # Narrow down part of dataframe you want here
  #
  #mf = dataframe.copy()
  mf = getHistoryForFacation(faction).copy() #  dataframe[dataframe['faction']== faction].copy()


  #
  # Convert to monthly and clean
  #
  mf['updated'] = pd.to_datetime(mf.updated, unit='ms')
  mf['updated'] = pd.to_datetime(mf.updated).dt.to_period('W').dt.to_timestamp()
  mf = mf.drop_duplicates(subset=['system', 'faction', 'updated'])
  hurm = mf.groupby(['updated','faction']).count().reset_index()

  labels = {'x':'Day', 'y':"Total Systems"}
  #foo = hurm[hurm['faction']== faction]
  foo = hurm
  fig = go.Figure(data=go.Scatter(x=foo.updated, y=foo.system, mode='lines+markers'))

  #fig = go.Figure()
  #factions = hurm['faction'].unique().tolist()
  #for fac in factions:
  #  foo = hurm[hurm['faction']== fac]
  #  stage3 = foo[['system','faction','updated']].groupby(['updated']).count().reset_index()
  #  fig.add_trace(go.Scatter(x=stage3['updated'], y=stage3['count'],
  #                  mode='lines',
  #                  stackgroup="b",
  #                  name=fac,
  #                  stackgaps="interpolate"))

  #if titleSubject is None:
  #  titleSubject = "+".join(factions)

  title = f"System Presences of {faction}"
  fig.update_layout(title=title,
                    xaxis_title="Date",
                    yaxis_title="Total Systems")
  #getScroller(fig)
  return fig

In [70]:
  #mf = dataframe.copy()
  #mf['updated'] = pd.to_datetime(mf.updated).dt.to_period('M').dt.to_timestamp()
  #mf = mf.drop_duplicates(subset=['system', 'faction', 'updated'])
  #hurm = mf.groupby(['updated','faction']).count().reset_index()
  #hurm

In [71]:
factionPresenceGraph("Pleiades Resource Enterprise")

In [72]:
factionPresenceGraph("Sirius Mining Merope")

In [73]:
factionPresenceGraph("Sirius Hyperspace")

In [76]:
def regionPresenceGraph( faction: str, region: int):
  hist = History()
  #
  # Narrow down part of dataframe you want here
  #
  mf = getHistoryForRegion(region).copy()
  #mf = dataframe[dataframe['region']== region].copy()


  #
  # Convert to monthly and clean
  #
  mf['updated'] = pd.to_datetime(mf.updated, unit='ms')
  mf['updated'] = pd.to_datetime(mf.updated).dt.to_period('W').dt.to_timestamp()
  mf = mf.drop_duplicates(subset=['system', 'faction', 'updated'])
  hurm = mf.groupby(['updated']).count().reset_index()

  labels = {'x':'Day', 'y':"Total Systems"}
  #foo = hurm[hurm['faction']== faction]
  foo = hurm
  fig = go.Figure(data=go.Scatter(x=foo.updated, y=foo.system, mode='lines+markers'))

  #fig = go.Figure()
  #factions = hurm['faction'].unique().tolist()
  #for fac in factions:
  #  foo = hurm[hurm['faction']== fac]
  #  stage3 = foo[['system','faction','updated']].groupby(['updated']).count().reset_index()
  #  fig.add_trace(go.Scatter(x=stage3['updated'], y=stage3['count'],
  #                  mode='lines',
  #                  stackgroup="b",
  #                  name=fac,
  #                  stackgaps="interpolate"))

  #if titleSubject is None:
  #  titleSubject = "+".join(factions)

  title = f"System Presences of {faction}"
  fig.update_layout(title=title,
                    xaxis_title="Date",
                    yaxis_title="Total Systems")
  #getScroller(fig)
  return fig

In [77]:
regionPresenceGraph("Sirius Hyperspace",2)

In [ ]:
  mf = dataframe[dataframe['region']== 1].copy()


  #
  # Convert to monthly and clean
  #
  mf['updated'] = pd.to_datetime(mf.updated, unit='ms')
  mf['updated'] = pd.to_datetime(mf.updated).dt.to_period('M').dt.to_timestamp()
  #mf = mf[ mf.loc[mf.groupby(['system','faction','updated').B.idxmin()]
  mf = mf.drop_duplicates(subset=['system', 'faction', 'updated'])
  hurm = mf.groupby(['updated']).count().reset_index()
hurm

In [102]:
def allClubFactionsGraph( ):


  mf = getHistoryByWeek().copy()
  hurm = mf.groupby(['updated','faction']).count().reset_index()

  labels = {'x':'Day', 'y':"Total Systems"}


  fig = go.Figure()
  factions = hurm['faction'].unique().tolist()
  for fac in factions:
    foo = hurm[ (hurm['faction']== fac) & (hurm['updated'] > '2019/12/01') ]
    fig.add_trace(go.Scatter(x=foo['updated'], y=foo['system'],
                    mode='lines',
                    stackgroup="b",
                    name=fac,
                    stackgaps="interpolate"))

  #if titleSubject is None:
  #  titleSubject = "+".join(factions)

  title = f"Club System Presences"
  fig.update_layout(title=title,
                    xaxis_title="Date",
                    yaxis_title="Total Systems")
  getScroller(fig)
  return fig

In [103]:
allClubFactionsGraph( )

In [ ]:
  mf = dataframe.copy()
  #mf = dataframe[dataframe['region']== 1].copy()


  #
  # Convert to monthly and clean
  #
  mf['updated'] = pd.to_datetime(mf.updated, unit='ms')
  mf['updated'] = pd.to_datetime(mf.updated).dt.to_period('W').dt.to_timestamp()
  mf = mf.drop_duplicates(subset=['system', 'faction', 'updated'])
  hurm = mf.groupby(['updated','faction']).count().reset_index()
  hurm

In [ ]:
def getSmallFrame(dateStr: str, faction, system):
  date_time_str = dateStr + " 00:00:00" #'2020-10-05 00:00:00'
  date_time_obj = dt.datetime.strptime(date_time_str, '%Y-%m-%d %H:%M:%S')

  df2 = dataframe.copy()
  df2 = df2[ (df2['faction']== faction) & (df2['system']==system)]
  #
  # Convert to daily and clean
  #
  df2['updated'] = pd.to_datetime(df2.updated, unit='ms')
  df2['updated'] = pd.to_datetime(df2.updated).dt.to_period('D').dt.to_timestamp()
  df2 = df2[ df2['updated']>= date_time_obj]
  df2 = df2.drop_duplicates(subset=['system', 'faction', 'updated'])
  return df2.sort_values(['updated'])

In [ ]:
df2 = getSmallFrame("2020-10-05","Sirius Hyperspace","Mooramba")
df2

In [ ]:
from craid.eddb.faction.Strategy import Strategy
from craid.eddb.faction.Simulation import Simulation

strat = Strategy()
theSim = Simulation(strat)
sim = theSim.getDatedSimulationFrame( date_time_obj, 31.1, 39.2,2752)
fig = theSim.getSimulationFigure(sim)
fig.show()

In [ ]:
fig.add_trace(go.Scatter(x=df2.updated, y=df2.influence,
                                 mode='lines',
                                 name='Target Actual',
                                 marker_color='magenta'))

In [ ]:
date_time_obj = dt.datetime.strptime("2020-10-01", '%Y-%m-%d')
sim = theSim.getDatedSimulationFrame( date_time_obj, 15.62, 41.8,2200)
fig = theSim.getSimulationFigure(sim)
fig.show()

In [ ]:
#57.4 6.89 5 oct  2752 pop

In [ ]:
fr = getSmallFrame("2020-10-01", "Sirius Hyperspace", "Daik")
fr

In [ ]:
fig.add_trace(go.Scatter(x=fr.updated, y=fr.influence,
                                 mode='lines',
                                 name='Target Actual',
                                 marker_color='magenta'))

In [ ]:
hist.getRawDataFrame()

In [ ]:
getHistoryForFacationAndSystem("Sirius Hyperspace","Daik")

In [ ]:
getLatestInfluences()

In [ ]:
# These are PROBABLE/POSSIBLE RETREATS
stage1[ stage1['updated']< "10/1/2020"].sort_values("influence")

In [99]:
getHistoryByWeek()

system  ...       week
0                            Abroin  ... 2018-06-25
1                            Abroin  ... 2018-07-30
2                            Abroin  ... 2018-08-27
3                            Abroin  ... 2018-10-01
4                            Abroin  ... 2018-10-29
5                            Abroin  ... 2018-11-26
6                            Abroin  ... 2018-12-31
7                            Abroin  ... 2019-04-01
8                            Abroin  ... 2019-04-29
9                            Abroin  ... 2019-05-27
10                           Abroin  ... 2019-07-01
11                           Abroin  ... 2019-10-28
12                           Abroin  ... 2019-11-25
13                           Abroin  ... 2019-12-30
14                           Abroin  ... 2020-01-27
15                           Abroin  ... 2020-02-24
16                           Abroin  ... 2020-03-30
17                           Abroin  ... 2020-04-27
3461                         Abroin  ... 2020-05-18
3462                         Abroin  ... 2020-06-08
6406                         Abroin  ... 2020-06-22
7115                         Abroin  ... 2020-06-29
7579                         Abroin  ... 2020-07-06
8371                         Abroin  ... 2020-07-13
9503                         Abroin  ... 2020-07-20
9967                         Abroin  ... 2020-07-27
10607                        Abroin  ... 2020-08-03
13842                        Abroin  ... 2020-08-31
15531                        Abroin  ... 2020-09-14
16063                        Abroin  ... 2020-09-21
18072                        Abroin  ... 2020-10-12
18616                        Abroin  ... 2020-10-19
18                           Baiame  ... 2018-06-25
19                           Baiame  ... 2018-07-30
20                           Baiame  ... 2018-10-01
21                           Baiame  ... 2019-04-29
22                           Baiame  ... 2019-05-27
23                           Baiame  ... 2019-07-01
24                           Baiame  ... 2019-07-29
25                           Baiame  ... 2019-09-30
3676                         Baiame  ... 2020-04-06
3678                         Baiame  ... 2020-06-01
3680                         Baiame  ... 2020-06-08
3681                         Baiame  ... 2020-06-15
9631                         Baiame  ... 2020-07-27
16069                        Baiame  ... 2020-09-21
16502                        Baiame  ... 2020-09-28
17023                        Baiame  ... 2020-10-05
18188                        Baiame  ... 2020-10-12
18413                        Baiame  ... 2020-10-19
26                          Carunda  ... 2019-04-29
27                          Carunda  ... 2019-07-01
28                          Carunda  ... 2019-08-26
29                          Carunda  ... 2019-10-28
30                          Carunda  ... 2019-11-25
31                          Carunda  ... 2019-12-30
32                          Carunda  ... 2020-01-27
33                          Carunda  ... 2020-04-27
3780                        Carunda  ... 2020-05-18
3781                        Carunda  ... 2020-06-08
3783                        Carunda  ... 2020-06-15
6769                        Carunda  ... 2020-06-29
9162                        Carunda  ... 2020-07-20
10824                       Carunda  ... 2020-08-03
11075                       Carunda  ... 2020-08-10
16828                       Carunda  ... 2020-10-05
17551                       Carunda  ... 2020-10-12
18190                       Carunda  ... 2020-10-19
34                        HIP 66267  ... 2019-05-27
35                        HIP 66267  ... 2019-11-25
36                        HIP 66267  ... 2019-12-30
4440                      HIP 66267  ... 2020-05-11
4441                      HIP 66267  ... 2020-05-25
4442                      HIP 66267  ... 2020-06-08
4443                      HIP 66267  ... 2020-06-15
4445                      HIP 66267  ... 2020-06-22
7133                     

In [95]:
getHistoryByMonth()

system  ...      month
0                            Abroin  ... 2018-07-01
1                            Abroin  ... 2018-08-01
2                            Abroin  ... 2018-09-01
3                            Abroin  ... 2018-10-01
4                            Abroin  ... 2018-11-01
5                            Abroin  ... 2018-12-01
6                            Abroin  ... 2019-01-01
7                            Abroin  ... 2019-04-01
8                            Abroin  ... 2019-05-01
9                            Abroin  ... 2019-06-01
10                           Abroin  ... 2019-07-01
11                           Abroin  ... 2019-11-01
12                           Abroin  ... 2019-12-01
13                           Abroin  ... 2020-01-01
14                           Abroin  ... 2020-02-01
15                           Abroin  ... 2020-03-01
16                           Abroin  ... 2020-04-01
3461                         Abroin  ... 2020-05-01
6406                         Abroin  ... 2020-06-01
9967                         Abroin  ... 2020-07-01
10607                        Abroin  ... 2020-08-01
16063                        Abroin  ... 2020-09-01
18616                        Abroin  ... 2020-10-01
18                           Baiame  ... 2018-07-01
19                           Baiame  ... 2018-08-01
20                           Baiame  ... 2018-10-01
21                           Baiame  ... 2019-05-01
22                           Baiame  ... 2019-06-01
23                           Baiame  ... 2019-07-01
24                           Baiame  ... 2019-08-01
25                           Baiame  ... 2019-10-01
3676                         Baiame  ... 2020-04-01
3681                         Baiame  ... 2020-06-01
9631                         Baiame  ... 2020-07-01
16069                        Baiame  ... 2020-09-01
18413                        Baiame  ... 2020-10-01
26                          Carunda  ... 2019-05-01
27                          Carunda  ... 2019-07-01
28                          Carunda  ... 2019-09-01
29                          Carunda  ... 2019-11-01
30                          Carunda  ... 2019-12-01
31                          Carunda  ... 2020-01-01
32                          Carunda  ... 2020-02-01
3780                        Carunda  ... 2020-05-01
3783                        Carunda  ... 2020-06-01
9162                        Carunda  ... 2020-07-01
11075                       Carunda  ... 2020-08-01
18190                       Carunda  ... 2020-10-01
34                        HIP 66267  ... 2019-06-01
35                        HIP 66267  ... 2019-12-01
36                        HIP 66267  ... 2020-01-01
4441                      HIP 66267  ... 2020-05-01
4445                      HIP 66267  ... 2020-06-01
9522                      HIP 66267  ... 2020-07-01
11089                     HIP 66267  ... 2020-08-01
18311                     HIP 66267  ... 2020-10-01
37                        HIP 67109  ... 2018-07-01
38                        HIP 67109  ... 2018-09-01
39                        HIP 67109  ... 2018-12-01
40                        HIP 67109  ... 2019-01-01
41                        HIP 67109  ... 2019-02-01
42                        HIP 67109  ... 2019-05-01
43                        HIP 67109  ... 2019-07-01
44                        HIP 67109  ... 2019-09-01
45                        HIP 67109  ... 2019-11-01
46                        HIP 67109  ... 2020-02-01
47                        HIP 67109  ... 2020-04-01
4446                      HIP 67109  ... 2020-05-01
4451                      HIP 67109  ... 2020-06-01
9399                      HIP 67109  ... 2020-07-01
14085                     HIP 67109  ... 2020-09-01
48                        HIP 68796  ... 2019-07-01
49                        HIP 68796  ... 2019-08-01
50                        HIP 68796  ... 2019-12-01
51                        HIP 68796  ... 2020-01-01
52                        HIP 68796  ... 2020-02-01
4452                     